In [1]:
!pip install -qU langsmith langchain-core langchain-community langchain-openai langchain-qdrant

In [2]:
!pip install -qU pypdf ragas

ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
unstructured-client 0.25.4 requires dataclasses-json>=0.6.4, but you have dataclasses-json 0.5.14 which is incompatible.


We'll need to provide our LangSmith API key, and set tracing to "true".

In [ ]:
import os
import getpass

os.environ["LANGCHAIN_TRACING_V2"] = "true"
os.environ["LANGCHAIN_API_KEY"] = getpass.getpass("LangChain API Key:")

LangChain API Key:··········


We'll also want to set a project name to make things easier for ourselves.

In [ ]:
from uuid import uuid4

os.environ["LANGCHAIN_PROJECT"] = f"AIM - SDG - {uuid4().hex[0:8]}"

OpenAI's API Key!

In [3]:
import os
import getpass

os.environ["OPENAI_API_KEY"] = getpass.getpass("OpenAI API Key:")

## Task 2: Loading Source Documents

In order to create a synthetic dataset, we must first load our source documents!

In [5]:
pdf_path = "easton_park.pdf"

documents = PyPDFLoader(pdf_path).load()

In [5]:
pdf_paths = [
    "AI_Risk_Management_Framework.pdf",
    "Blueprint-for-an-AI-Bill-of-Rights.pdf",
]

In [7]:
from langchain_community.document_loaders import PyPDFLoader
pdf_documents = []
for pdf_path in pdf_paths:
    loader = PyPDFLoader(pdf_path)
    pdf_documents.extend(loader.load())

In [13]:
pdf_documents[-1]

Document(metadata={'source': 'Blueprint-for-an-AI-Bill-of-Rights.pdf', 'page': 72}, page_content=' ENDNOTES\n107. Centers for Medicare & Medicaid Services. Biden-Harris Administration Quadruples the Number\nof Health Care Navigators Ahead of HealthCare.gov Open Enrollment Period. Aug. 27, 2021.\nhttps://www.cms.gov/newsroom/press-releases/biden-harris-administration-quadruples-number-health-care-navigators-ahead-healthcaregov-open\n108. See, e.g., McKinsey & Company. The State of Customer Care in 2022. July 8, 2022. https://\nwww.mckinsey.com/business-functions/operations/our-insights/the-state-of-customer-care-in-2022;\nSara Angeles. Customer Service Solutions for Small Businesses. Business News Daily.\nJun. 29, 2022. https://www.businessnewsdaily.com/7575-customer-service-solutions.html\n109. Mike Hughes. Are We Getting The Best Out Of Our Bots? Co-Intelligence Between Robots &\nHumans. Forbes. Jul. 14, 2022.\nhttps://www.forbes.com/sites/mikehughes1/2022/07/14/are-we-getting-the-bes

In [21]:
from ragas.testset.generator import TestsetGenerator
from ragas.testset.evolutions import simple, reasoning, multi_context
from langchain_openai import ChatOpenAI, OpenAIEmbeddings

generator_llm = ChatOpenAI(model="gpt-4")
critic_llm = ChatOpenAI(model="gpt-4o-mini")
embeddings = OpenAIEmbeddings()

generator = TestsetGenerator.from_langchain(
    generator_llm,
    critic_llm,
    embeddings
)

distributions = {
    simple: 0.5,
    multi_context: 0.4,
    reasoning: 0.1
}

In [22]:
testset = generator.generate_with_langchain_docs(pdf_documents, 25, distributions, with_debugging_logs=True)

embedding nodes:   0%|          | 0/284 [00:00<?, ?it/s]

[ragas.testset.extractor.DEBUG] topics: {'keyphrases': ['Data privacy', 'Automated systems', 'Sensitive data', 'Ethical review', 'Data quality', 'Access to sensitive data', 'Public reporting']}
[ragas.testset.extractor.DEBUG] topics: {'keyphrases': ['Data privacy', 'Automated systems', 'Sensitive data', 'Ethical review', 'Data quality', 'Access to sensitive data', 'Public reporting']}
[ragas.testset.extractor.DEBUG] topics: {'keyphrases': ['Digital surveillance', 'Federal Trade Commission', 'Data collection on children', 'Privacy Framework', 'Facial recognition in schools']}
[ragas.testset.extractor.DEBUG] topics: {'keyphrases': ['Digital surveillance', 'Federal Trade Commission', 'Data collection on children', 'Privacy Framework', 'Facial recognition in schools']}
[ragas.testset.extractor.DEBUG] topics: {'keyphrases': ['Participatory Engagement Methods', 'Field Testing', 'AI Red-teaming', 'Feedback activities', 'AI risk management']}
[ragas.testset.extractor.DEBUG] topics: {'keyphrase

Generating:   0%|          | 0/25 [00:00<?, ?it/s]

[ragas.testset.filters.DEBUG] context scoring: {'clarity': 1, 'depth': 2, 'structure': 2, 'relevance': 3, 'score': 2.0}
[ragas.testset.filters.DEBUG] context scoring: {'clarity': 1, 'depth': 2, 'structure': 2, 'relevance': 3, 'score': 2.0}
[ragas.testset.filters.DEBUG] context scoring: {'clarity': 1, 'depth': 2, 'structure': 2, 'relevance': 3, 'score': 2.0}
[ragas.testset.evolutions.DEBUG] keyphrases in merged node: ['Stakeholder communities input', 'AI RMF Map function', 'GAI risks', 'Organizational risk tolerances', 'Transparent policies and procedures']
[ragas.testset.evolutions.DEBUG] keyphrases in merged node: ['Stakeholder communities input', 'AI RMF Map function', 'GAI risks', 'Organizational risk tolerances', 'Transparent policies and procedures']
[ragas.testset.evolutions.DEBUG] keyphrases in merged node: ['Stakeholder communities input', 'AI RMF Map function', 'GAI risks', 'Organizational risk tolerances', 'Transparent policies and procedures']
[ragas.testset.filters.DEBUG] c

In [23]:
testset.to_pandas()

question  \
0   What is the significance of providing notice a...   
1   How can structured human feedback exercises, s...   
2   How do measurement gaps between laboratory and...   
3   How should data collection and use-case scope ...   
4   What action did the Federal Trade Commission t...   
5   How should explanatory mechanisms be built int...   
6   What are some examples of GAI risks that organ...   
7   How should the validity of explanations provid...   
8   How do generative models like LLMs generate ou...   
9   How can appropriate diligence on training data...   
10  How do integrated human-AI systems benefit com...   
11  What was the purpose of the year of public eng...   
12  How can automated systems prevent 'mission cre...   
13  How can GAI tech improve red-teaming with huma...   
14  Why is it important for lenders to inform cons...   
15  Why is public transparency important in automa...   
16  How can governance principles manage risks of ...   
17  Why is accuracy important in reviewing and doc...   
18  How can feedback be used to gather user input ...   
19  What measures are being taken to address issue...   
20  How do ballot curing laws help voters fix ball...   
21  How can feedback and red-teaming assess GAI eq...   
22  How can algorithmic discrimination be prevente...   
23  How can system design ensure behavior transpar...   

                                             contexts  \
0   [    \n \n NOTICE & \nEXPLANATION \nWHY THIS P...   
1   [ \n29 MS-1.1-006 Implement continuous monitor...   
2   [ \n49 early lifecycle TEVV approaches are dev...   
3   [      DATA PRIVACY \nWHAT SHOULD BE EXPECTED ...   
4   [ \n \n ENDNOTES\n75. See., e.g., Sam Sabin. D...   
5   [      NOTICE & \nEXPLANATION \nWHAT SHOULD BE...   
6   [ \n15 GV-1.3-004 Obtain input from stakeholde...   
7   [      NOTICE & \nEXPLANATION \nWHAT SHOULD BE...   
8   [ \n6 2.2. Confabulation  \n“Confabulation” re...   
9   [ \n27 MP-4.1-0 10 Conduct appropriate diligen...   
10  [       \n   \n \n \n \n \n HUMAN ALTERNATIVES...   
11  [ \n \n  \n  \n \n \n \n \n \n \n \n About thi...   
12  [      DATA PRIVACY \nWHAT SHOULD BE EXPECTED ...   
13  [ \n51 general public participants. For exampl...   
14  [       \n \n      \n \n  \n  \n \n      \n \n...   
15  [    \n \n NOTICE & \nEXPLANATION \nWHY THIS P...   
16  [ \n47 Appendix A.  Primary GAI Considerations...   
17  [ \n25 MP-2.3-002 Review and document accuracy...   
18  [ \n41 MG-2.2-0 06 Use feedback from internal ...   
19  [    WHY THIS PRINCIPLE IS IMPORTANT\nThis sec...   
20  [       \n   \n \n \n \n \n HUMAN ALTERNATIVES...   
21  [ \n29 MS-1.1-006 Implement continuous monitor...   
22  [ ALGORITHMIC DISCRIMINATION Protections\nYou ...   
23  [      NOTICE & \nEXPLANATION \nWHAT SHOULD BE...   

                                         ground_truth evolution_type  \
0   Providing notice and explanation as a legal re...         simple   
1   Structured human feedback exercises, such as G...         simple   
2   Measurement gaps between laboratory and real-w...         simple   
3   Data collection and use-case scope limits in a...         simple   
4   FTC sued Kochava for selling data that tracks ...         simple   
5   In settings where the consequences are high as...         simple   
6   Organizations need to consider various GAI ris...         simple   
7   The explanation provided by a system should ac...         simple   
8   Generative models like LLMs generate outputs t...         simple   
9   Appropriate diligence on training data use can...         simple   
10  Integrated human-AI systems benefit companies ...         simple   
11  The purpose of the year of public engagement t...         simple   
12  Automated systems can prevent 'mission creep' ...  multi_context   
13  GAI technologies can improve red-teaming with ...  multi_context   
14  It is important for lenders to inform consumer...  multi_context   
15  Public transparency is crucial in aut

In [24]:
df = testset.to_pandas()
df.to_csv("synthetic_midterm_question_dataset.csv", index=False)